In [1]:
#import libraries
import pandas as pd
import json
import re
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import requests
import warnings
import pprint
warnings.simplefilter('ignore')

In [2]:
url ='https://api.spoonacular.com/recipes/complexSearch?apiKey&query=Fish&addRecipeInformation=True&addRecipeNutrition=True&number=100'
new_res= requests.get(url).json()
#new_res  

{'results': [{'vegetarian': False,
   'vegan': False,
   'glutenFree': True,
   'dairyFree': True,
   'veryHealthy': False,
   'cheap': False,
   'veryPopular': False,
   'sustainable': False,
   'weightWatcherSmartPoints': 10,
   'gaps': 'no',
   'lowFodmap': False,
   'aggregateLikes': 1,
   'spoonacularScore': 74.0,
   'healthScore': 40.0,
   'creditsText': 'Foodista.com – The Cooking Encyclopedia Everyone Can Edit',
   'license': 'CC BY 3.0',
   'sourceName': 'Foodista',
   'pricePerServing': 320.77,
   'id': 642929,
   'title': 'Fish Congee',
   'readyInMinutes': 160,
   'servings': 4,
   'sourceUrl': 'http://www.foodista.com/recipe/NK4B7FW4/fish-congee',
   'image': 'https://spoonacular.com/recipeImages/642929-312x231.jpg',
   'imageType': 'jpg',
   'nutrition': {'nutrients': [{'name': 'Calories',
      'amount': 440.73,
      'unit': 'kcal',
      'percentOfDailyNeeds': 22.04},
     {'name': 'Fat', 'amount': 5.16, 'unit': 'g', 'percentOfDailyNeeds': 7.93},
     {'name': 'Saturat

In [3]:
recipe5_df=pd.json_normalize(new_res,record_path=['results'])
recipe5_df.head(3)

vegetarian  vegan  glutenFree  dairyFree  veryHealthy  cheap  veryPopular  \
0       False  False        True       True        False  False        False   
1       False  False        True       True        False  False        False   
2       False  False       False      False        False  False        False   

   sustainable  weightWatcherSmartPoints gaps  ...  \
0        False                        10   no  ...   
1        False                         2   no  ...   
2        False                        10   no  ...   

                                nutrition.flavonoids  \
0  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   
1  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   
2  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   

                               nutrition.ingredients  \
0  [{'id': 15015, 'name': 'cod filet', 'amount': ...   
1  [{'id': 2048, 'name': 'apple cider vinegar', '...   
2  [{'id': 18079, 'name': 'bread crumbs', 'amount...   

   nutrition.caloricBreakdown.percentProtein  \
0                                      34.13   
1                                      62.98   
2                                      25.42   

   nutrition.caloricBreakdown.percentFat  \
0                                  10.98   
1                                  11.00   
2                                  46.40   

  nutrition.caloricBreakdown.percentCarbs nutrition.weightPerServing.amount  \
0                                   54.89                               769   
1                                   26.02                               142   
2                                   28.18                               224   

  nutrition.weightPerServing.unit  author  preparationMinutes cookingMinutes  
0                               g     NaN                 NaN            NaN  
1                               g     NaN                 NaN            NaN  
2                               g     NaN                 NaN            NaN  

[3 rows x 44 columns]

In [4]:
recipe5_df.drop(columns=['vegetarian', 'vegan', 'glutenFree', 'dairyFree', 'veryHealthy', 'cheap', 'veryPopular', 'sustainable', 'weightWatcherSmartPoints', 'gaps', 'lowFodmap', 'aggregateLikes', 'spoonacularScore',
                      'healthScore', 'creditsText', 'license', 'sourceName', 'pricePerServing','sourceUrl','imageType','summary','diets', 'occasions','spoonacularSourceUrl','nutrition.properties','nutrition.flavonoids','nutrition.caloricBreakdown.percentProtein','nutrition.caloricBreakdown.percentFat','nutrition.caloricBreakdown.percentCarbs','nutrition.weightPerServing.amount',
                      'nutrition.weightPerServing.unit','preparationMinutes','cookingMinutes','author','nutrition.nutrients','nutrition.ingredients'],inplace=True)
#recipe5_df.head()

# One hot encoding dishType column

In [5]:
recipe5_df['dish']=0
recipe5_df.columns

Index(['id', 'title', 'readyInMinutes', 'servings', 'image', 'cuisines',
       'dishTypes', 'analyzedInstructions', 'dish'],
      dtype='object')

In [6]:
for i in range(0,100):
    item =recipe5_df['dishTypes'][i]
    if len(item)==0:
        recipe5_df.iloc[i,8]=0
        
    else:
        #print(item[0])
        
        if any(x in ['lunch', 'dinner', 'antipasti','side dish','salad'] for x in item):
            #print(f"{i}:lunch")
            recipe5_df.iloc[i,8]=1
        if any(x in ['breakfast', 'bread'] for x in item):
            recipe5_df.iloc[i,8]=0
#recipe5_df

In [7]:
recipe5_df.drop(columns=['dishTypes'],inplace=True)
recipe5_df.head(3)

id                      title  readyInMinutes  servings  \
0  642929                Fish Congee             160         4   
1    4273           Fish Hunan Style              62         8   
2  642927  Fish Crocchette Appetizer              45         8   

                                               image cuisines  \
0  https://spoonacular.com/recipeImages/642929-31...       []   
1  https://spoonacular.com/recipeImages/4273-312x...       []   
2  https://spoonacular.com/recipeImages/642927-31...       []   

                                analyzedInstructions  dish  
0  [{'name': '', 'steps': [{'number': 1, 'step': ...     1  
1  [{'name': '', 'steps': [{'number': 1, 'step': ...     1  
2  [{'name': '', 'steps': [{'number': 1, 'step': ...     1

In [8]:
#Getting ingredients for each recipe
#Ingredients is a list of dictionaries in nutrition key
ingredients_list=[]
recipe_idlist=[]

for recipe in new_res['results']:
    recipe_id =recipe['id']
    ingres=recipe['nutrition']['ingredients']
    ingri_dict={}
    for ingredient_dict in ingres:
        name=ingredient_dict['name']
        amount=ingredient_dict['amount']
        unit=ingredient_dict['unit']
        value=str(round(amount,2))+' '+unit 
        ingri_dict[name]=value
    ingredients_list.append(ingri_dict)
    recipe_idlist.append(recipe_id)    

In [9]:
ingredient_names=[]
for i in range(0,100):
    ingredients=list(ingredients_list[i])
    ingredient_names.append(ingredients)
len(ingredient_names)

100

In [10]:
recipe5_df['ingredients']=ingredients_list

In [11]:
recipe5_df['grocery']=ingredient_names
recipe5_df.head(3)

id                      title  readyInMinutes  servings  \
0  642929                Fish Congee             160         4   
1    4273           Fish Hunan Style              62         8   
2  642927  Fish Crocchette Appetizer              45         8   

                                               image cuisines  \
0  https://spoonacular.com/recipeImages/642929-31...       []   
1  https://spoonacular.com/recipeImages/4273-312x...       []   
2  https://spoonacular.com/recipeImages/642927-31...       []   

                                analyzedInstructions  dish  \
0  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   
1  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   
2  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   

                                         ingredients  \
0  {'cod filet': '0.38 pounds', 'ginger': '0.25 p...   
1  {'apple cider vinegar': '0.38 Tbsps', 'brown s...   
2  {'bread crumbs': '1.0 servings', 'canola oil':...   

                                             grocery  
0  [cod filet, ginger, oyster sauce, rice, rice w...  
1  [apple cider vinegar, brown sugar, cod fish fi...  
2  [bread crumbs, canola oil, cod fillet, eggs, f...

# Extracting Instructions

In [12]:
recipe_instructions=recipe5_df[['analyzedInstructions','id']]
recipe_instructions.head

<bound method NDFrame.head of                                  analyzedInstructions      id
0   [{'name': '', 'steps': [{'number': 1, 'step': ...  642929
1   [{'name': '', 'steps': [{'number': 1, 'step': ...    4273
2   [{'name': '', 'steps': [{'number': 1, 'step': ...  642927
3   [{'name': '', 'steps': [{'number': 1, 'step': ...  642941
4   [{'name': '', 'steps': [{'number': 1, 'step': ...  642977
..                                                ...     ...
95  [{'name': '', 'steps': [{'number': 1, 'step': ...  643789
96  [{'name': '', 'steps': [{'number': 1, 'step': ...  663177
97  [{'name': '', 'steps': [{'number': 1, 'step': ...  642096
98  [{'name': '', 'steps': [{'number': 1, 'step': ...  636256
99  [{'name': '', 'steps': [{'number': 1, 'step': ...  648279

[100 rows x 2 columns]>

In [13]:
recipe_inst=[]
for instructions,ids in zip(list(recipe_instructions['analyzedInstructions'].values),list(recipe_instructions['id'].values)):
    #print(instructions,ids)
    #print(instructions[0]['steps'])
    instruct={}
    recipe_step=''
    try:
    #break   
        for no_steps in range(len(instructions[0]['steps'])):
            #print(no_steps)
            recipe_step+=instructions[0]['steps'][no_steps]['step']    
            #break
            #print(recipe_step)
        instruct[ids]=recipe_step
        #print(instruct)
        recipe_inst.append(instruct)
    except:
        pass

In [14]:
instruction_final=pd.DataFrame()
for dict_recipe in recipe_inst:
    df=pd.DataFrame(dict_recipe,index=dict_recipe.keys())
    df.columns=['instructions']
    #print(df)
    #break
    instruction_final=pd.concat([instruction_final,df],ignore_index=False,axis=0)

In [15]:
instruction_final.index.names = ['id']
#instruction_final

In [16]:
recipe5_df=recipe5_df.merge(instruction_final,on='id')
recipe5_df.drop(columns=['analyzedInstructions'],inplace=True)

In [17]:
recipe5_df.head(3)

id                      title  readyInMinutes  servings  \
0  642929                Fish Congee             160         4   
1    4273           Fish Hunan Style              62         8   
2  642927  Fish Crocchette Appetizer              45         8   

                                               image cuisines  dish  \
0  https://spoonacular.com/recipeImages/642929-31...       []     1   
1  https://spoonacular.com/recipeImages/4273-312x...       []     1   
2  https://spoonacular.com/recipeImages/642927-31...       []     1   

                                         ingredients  \
0  {'cod filet': '0.38 pounds', 'ginger': '0.25 p...   
1  {'apple cider vinegar': '0.38 Tbsps', 'brown s...   
2  {'bread crumbs': '1.0 servings', 'canola oil':...   

                                             grocery  \
0  [cod filet, ginger, oyster sauce, rice, rice w...   
1  [apple cider vinegar, brown sugar, cod fish fi...   
2  [bread crumbs, canola oil, cod fillet, eggs, f...   

                                        instructions  
0  In a big pot (a cocotte if you have one), put ...  
1  Make marinade out of soy sauce, sherry (or vin...  
2  Begin to cook the fish and potatoes.Cook cod i...

In [18]:
#Saving 100 recipes dataframe to a csv
recipe5_df.to_csv('./all_recipes/recipe5.csv',index=False)

In [19]:
#scraping nutrition data

In [20]:
nutri_list =[]
id_list=[]
for recipe in new_res['results']:
    recipe_id =recipe['id']
    nutrients =recipe['nutrition']['nutrients']
    nutri_dict={}
    for nutrient_dict in nutrients:
        name = nutrient_dict['name']
        amount = nutrient_dict['amount']
        unit = nutrient_dict['unit']
        #value = str(round(amount,2))+' '+unit
        key=name+' '+unit
        nutri_dict[key]=amount
    nutri_list.append(nutri_dict)
    id_list.append(recipe_id)

In [21]:
nutrition5_df= pd.DataFrame(nutri_list,index=id_list)
nutrition5_df.index.name='recipe_id'
nutrition5_df.head(3)

Calories kcal  Fat g  Saturated Fat g  Carbohydrates g  \
recipe_id                                                           
642929            440.73   5.16             0.86            57.98   
4273              111.00   1.32             0.32             7.02   
642927            397.47  20.35             3.50            27.81   

           Net Carbohydrates g  Sugar g  Cholesterol mg  Sodium mg  Alcohol g  \
recipe_id                                                                       
642929                   56.72     0.41           73.14     628.48        0.6   
4273                      6.53     4.78           57.62     558.33        NaN   
642927                   25.64     2.68           79.08     513.40        NaN   

           Protein g  ...  Vitamin D µg  Vitamin B5 mg  Vitamin B2 mg  \
recipe_id             ...                                               
642929         36.05  ...          1.53           0.99           0.17   
4273           16.99  ...          0.88           0.27           0.12   
642927         25.09  ...          2.41           0.77           0.30   

           Vitamin E mg  Iron mg  Calcium mg  Folate µg  Fiber g  \
recipe_id                                                          
642929             1.25     1.48       71.25      24.01     1.25   
4273               1.01     0.87       29.69      11.16     0.49   
642927             3.23     2.65      167.42      63.39     2.17   

           Vitamin C mg  Vitamin A IU  
recipe_id                              
642929             3.06        127.90  
4273               1.50        375.85  
642927            20.55        798.49  

[3 rows x 32 columns]

In [22]:
print(nutrition5_df.duplicated().sum())

0


In [23]:
#saving the nutrition details of 100 recipes dataframe to csv
nutrition5_df.to_csv('./all_nutrition/nutrition5.csv',index=True)

In [24]:
#Defining dataframe for ingredients
ingres5_df=pd.DataFrame(ingredients_list,index= recipe_idlist)
ingres5_df.fillna(value=0,inplace=True)
ingres5_df.index.name='recipe_id'
ingres5_df.head(3)

cod filet      ginger     oyster sauce       rice  \
recipe_id                                                        
642929     0.38 pounds  0.25 piece  0.5 tablespoons  0.38 cups   
4273                 0           0                0          0   
642927               0           0                0          0   

                 rice wine          salt       sesame oil       shallot  \
recipe_id                                                                 
642929     0.25 tablespoon    0.25 pinch  0.25 tablespoon  1.0 servings   
4273                     0             0                0             0   
642927                   0  1.0 servings                0             0   

                soya sauce spring onions  ... flat leaf parsley  \
recipe_id                                 ...                     
642929     0.25 tablespoon  1.0 servings  ...                 0   
4273                     0             0  ...                 0   
642927                   0             0  ...                 0   

          kalamata olives lemongrass thai basil saltine crackers peppers  \
recipe_id                                                                  
642929                  0          0          0                0       0   
4273                    0          0          0                0       0   
642927                  0          0          0                0       0   

          old bay seasoning chillies parsley leaves pasta shells  
recipe_id                                                         
642929                    0        0              0            0  
4273                      0        0              0            0  
642927                    0        0              0            0  

[3 rows x 425 columns]

In [25]:
#saving the ingredients of 100 recipes dataframe to csv
ingres5_df.to_csv('./all_ingredients/ingredients5.csv',index=True)